In [1]:
import torch
import torch_geometric
import torch_scatter
import torch_sparse
import torch_cluster
import torch_spline_conv

print("✅ All PyG packages imported successfully!")


✅ All PyG packages imported successfully!


In [2]:
import torch
import numpy as np
from deeprobust.graph.data import Dataset
from deeprobust.graph.defense import GCN
from deeprobust.graph.global_attack import Metattack

data = Dataset(root='/tmp/', name='cora', setting='nettack')
adj, features, labels = data.adj, data.features, data.labels
idx_train, idx_val, idx_test = data.idx_train, data.idx_val, data.idx_test
idx_unlabeled = np.union1d(idx_val, idx_test)

Loading cora dataset...
Selecting 1 largest connected components


In [3]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
surrogate = GCN(nfeat=features.shape[1], nclass=labels.max().item()+1, nhid=64,
                with_relu=False, device=device)
surrogate = surrogate.to(device)
surrogate.fit(features, adj, labels, idx_train)

original_adj_dense = adj.copy()

/home/niyati/miniconda3/envs/ersp_v2/lib/python3.9/site-packages/deeprobust/graph/utils.py:356: UserWarning: torch.sparse.SparseTensor(indices, values, shape, *, device=) is deprecated.  Please use torch.sparse_coo_tensor(indices, values, shape, dtype=, device=). (Triggered internally at /pytorch/torch/csrc/utils/tensor_new.cpp:644.)
  return torch.sparse.FloatTensor(sparseconcat.t(),sparsedata,torch.Size(sparse_mx.shape))


In [4]:
model = Metattack(model=surrogate, nnodes=adj.shape[0], feature_shape=features.shape, device=device)
model = model.to(device)
perturbations = int(2.00 * (adj.sum() // 2))
model.attack(features, adj, labels, idx_train, idx_unlabeled, perturbations, ll_constraint=False)
modified_adj = model.modified_adj

# Convert modified adjacency tensor to numpy for comparison
if isinstance(modified_adj, torch.Tensor):
    modified_adj_dense = modified_adj.cpu().numpy()
else:
    modified_adj_dense = modified_adj.todense()


# Find added and removed edges
added_edges = []
removed_edges = []

for i in range(adj.shape[0]):
    for j in range(i + 1, adj.shape[0]):
        # Check if edge was added (wasn't in original but is in modified)
        if original_adj_dense[i, j] == 0 and modified_adj_dense[i, j] != 0:
            added_edges.append((i, j))
        # Check if edge was removed (was in original but not in modified)
        elif original_adj_dense[i, j] != 0 and modified_adj_dense[i, j] == 0:
            removed_edges.append((i, j))

# Combine into one list (optional)
all_perturbed_edges = added_edges + removed_edges

print(f"Added edges: {len(added_edges)}")
print(f"Removed edges: {len(removed_edges)}")
print(f"Total perturbed edges: {len(all_perturbed_edges)}")
print(f"Sample added edges: {added_edges[:5] if added_edges else 'None'}")
print(f"Sample removed edges: {removed_edges[:5] if removed_edges else 'None'}")

Perturbing graph:   0%|                                                                       | 0/10138 [00:00<?, ?it/s]

GCN loss on unlabled data: 0.5307369232177734
GCN acc on unlabled data: 0.8466696468484578
attack loss: 0.16740143299102783


Perturbing graph:   0%|                                                             | 1/10138 [00:01<5:21:53,  1.91s/it]

GCN loss on unlabled data: 0.5509267449378967
GCN acc on unlabled data: 0.8395172105498435
attack loss: 0.17309528589248657


Perturbing graph:   0%|                                                             | 2/10138 [00:03<4:16:04,  1.52s/it]

...

GCN loss on unlabled data: 16.734689712524414
GCN acc on unlabled data: 0.06928922664282522
attack loss: 8.67189884185791


Perturbing graph: 100%|████████████████████████████████████████████████████████▉| 10137/10138 [3:34:54<00:00,  1.04it/s]

GCN loss on unlabled data: 17.148935317993164
GCN acc on unlabled data: 0.07018328118015199
attack loss: 8.867029190063477


Perturbing graph: 100%|█████████████████████████████████████████████████████████| 10138/10138 [3:34:55<00:00,  1.27s/it]


Added edges: 9387
Removed edges: 751
Total perturbed edges: 10138
Sample added edges: [(1, 204), (1, 328), (1, 997), (1, 1264), (1, 1911)]
Sample removed edges: [(5, 2345), (8, 846), (9, 165), (9, 2218), (11, 1019)]


In [5]:
import os
save_path = os.path.join(os.getcwd(), "GreedySingle_Cora_edges_list.pth")
torch.save(all_perturbed_edges, save_path)


In [3]:
all_perturbed_edges = torch.load("GreedySingle_Cora_edges_list.pth")

In [4]:
print(len(all_perturbed_edges))

10138


NameError: name 'budget' is not defined

In [5]:
all_perturbed_edges

[(1, 204),
 (1, 328),
 (1, 997),
 (1, 1264),
 (1, 1911),
 (1, 2175),
 (2, 105),
 (2, 168),
 (2, 190),
 (2, 336),
 (2, 397),
 (2, 404),
 (2, 484),
 (2, 500),
 (2, 551),
 (2, 656),
 (2, 813),
 (2, 1110),
 (2, 1301),
 (2, 1413),
 (2, 1438),
 (2, 1461),
 (2, 1562),
 (2, 1716),
 (2, 1743),
 (2, 1755),
 (2, 1829),
 (2, 1884),
 (2, 2277),
 (2, 2315),
 (2, 2366),
 (2, 2460),
 (3, 286),
 (3, 360),
 (3, 543),
 (3, 584),
 (3, 676),
 (3, 766),
 (3, 909),
 (3, 968),
 (3, 1117),
 (3, 1315),
 (3, 1442),
 (3, 1630),
 (3, 1712),
 (3, 1962),
 (3, 2118),
 (3, 2157),
 (3, 2460),
 (4, 217),
 (4, 636),
 (4, 1345),
 (4, 1561),
 (4, 1675),
 (4, 1794),
 (4, 2165),
 (5, 464),
 (6, 526),
 (6, 2333),
 (7, 368),
 (7, 375),
 (7, 698),
 (7, 813),
 (7, 1937),
 (8, 134),
 (8, 285),
 (8, 1443),
 (8, 1629),
 (8, 2123),
 (9, 73),
 (9, 198),
 (9, 205),
 (9, 208),
 (9, 286),
 (9, 309),
 (9, 328),
 (9, 382),
 (9, 383),
 (9, 410),
 (9, 482),
 (9, 522),
 (9, 562),
 (9, 593),
 (9, 658),
 (9, 675),
 (9, 700),
 (9, 718),
 (9, 75

In [7]:
rm -rf ./Cora

In [11]:
import sys
import os
sys.path.append(os.path.abspath("../../"))
from torch.serialization import safe_globals
from torch_geometric.data import Data
from src.models.gcn import *
from src.utils.datasets import *
from src.models.trainable import *
from src.attacks.greedy_gd import *

from torch_geometric.utils import dense_to_sparse, to_networkx, from_networkx
import networkx as nx


# Allow torch.load to unpickle PyG's Data object
with safe_globals([Data]):
    from torch_geometric.datasets import Planetoid
    import torch

    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    cora_dataset = Planetoid(root='.', name='Cora')
    data = cora_dataset[0].to(device)
    print(data)

model = GCN(data.x.shape[1], cora_dataset.num_classes, [64]).to(device)

model.reset_parameters()
train = Trainable(model)
train.fit(data, 200)

initial_loss, initial_accuracy = train.test(data)
print(f"Initial Accuracy: {initial_accuracy}")
print(f"Initial Loss: {initial_loss}")

G = to_networkx(data, to_undirected=True)
initial_edge_count = G.number_of_edges() // 2
ptb_rate = 0.20
budget = int(ptb_rate * initial_edge_count)

Data(x=[2708, 1433], edge_index=[2, 10556], y=[2708], train_mask=[2708], val_mask=[2708], test_mask=[2708])
Epoch 0, Train Loss - 1.9548879861831665, Val Loss - 1.8153932094573975, Val Accuracy - 0.642
Epoch 20, Train Loss - 0.010420717298984528, Val Loss - 0.6404727101325989, Val Accuracy - 0.795
Epoch 40, Train Loss - 0.009407754987478256, Val Loss - 0.6305433511734009, Val Accuracy - 0.8
Epoch 60, Train Loss - 0.014831041917204857, Val Loss - 0.6044592261314392, Val Accuracy - 0.808
Epoch 80, Train Loss - 0.015662094578146935, Val Loss - 0.6224789023399353, Val Accuracy - 0.81
Epoch 100, Train Loss - 0.012205922976136208, Val Loss - 0.6061656475067139, Val Accuracy - 0.817
Epoch 120, Train Loss - 0.008816736750304699, Val Loss - 0.6365922689437866, Val Accuracy - 0.802
Epoch 140, Train Loss - 0.010110358707606792, Val Loss - 0.6321133971214294, Val Accuracy - 0.806
Epoch 160, Train Loss - 0.010072180069983006, Val Loss - 0.6436744928359985, Val Accuracy - 0.81
Epoch 180, Train Loss 

In [12]:
from src.attacks.greedy_gd import Metattack as MyMetattack
def two_phase_attack(split):
    diff_threshold = 0.01
    first_phase_edges = int(budget * split)
    second_phase_percent = ptb_rate * (1 - split) * 0.5
    print(f"\n--- Running split: {split} ---")
    print(f"Second phase perturbation rate: {second_phase_percent:.4f}")

    phase1_accuracies = []
    phase2_accuracies = []

    G = to_networkx(data, to_undirected=True)
    data_copy = copy.copy(data)

    i, j = 0, 0  # i - edges successfully added, j - index in list

    # === Phase 1 ===
    while i < first_phase_edges:
        if j >= len(all_perturbed_edges):
            print("Ran out of candidate edges in Phase 1. Moving to Phase 2.")
            break

        u, v = all_perturbed_edges[j]
        G.add_edge(u, v)

        modified_data = from_networkx(G).to(device)
        modified_data.x = data.x 
        modified_data.y = data.y 
        modified_data.train_mask = data.train_mask
        modified_data.test_mask = data.test_mask

        _, modified_accuracy = train.test(modified_data)

        if modified_accuracy == initial_accuracy:
            i += 1
            phase1_accuracies.append(modified_accuracy)
        else:
            G.remove_edge(u, v)

        j += 1

    print(f"Phase 1: Added {i} edges out of requested {first_phase_edges}.")

    # === Phase 2 ===
    modified_data = from_networkx(G).to(device)
    modified_data.x = data.x 
    modified_data.y = data.y 
    modified_data.train_mask = data.train_mask
    modified_data.test_mask = data.test_mask

    attacker = MyMetattack(modified_data, device=device)
    attacker.setup_surrogate(model,
                             labeled_nodes=data.train_mask,
                             unlabeled_nodes=data.test_mask, 
                             lambda_=0.)
    attacker.reset()
    attacker.attack(second_phase_percent)

    degs = defaultdict(tuple)
    for k, v in attacker._added_edges.items():
        degs[v] = (k, True)
    for k, v in attacker._removed_edges.items():
        degs[v] = (k, False)

    for _, second in degs.items():
        u, v = second[0]
        if second[1]:
            G.add_edge(u, v)
        else:
            G.remove_edge(u, v)

        modified_data = from_networkx(G).to(device)
        modified_data.x = data.x 
        modified_data.y = data.y 
        modified_data.train_mask = data.train_mask
        modified_data.test_mask = data.test_mask

        _, modified_accuracy = train.test(modified_data)
        phase2_accuracies.append(modified_accuracy)

    # === Final Reporting ===
    final_accuracy = phase2_accuracies[-1] if phase2_accuracies else (
        phase1_accuracies[-1] if phase1_accuracies else initial_accuracy)
    accuracy_drop = initial_accuracy - final_accuracy

    print(f"Final Accuracy: {final_accuracy:.4f}")
    print(f"Accuracy Drop: {accuracy_drop:.4f}")

    return {
        "split": split,
        "phase1_added": i,
        "phase1_accuracies": phase1_accuracies,
        "phase2_accuracies": phase2_accuracies,
        "final_accuracy": final_accuracy,
        "accuracy_drop": accuracy_drop
    }


In [14]:
from collections import defaultdict

splits = [0, 0.5]
split_dic = defaultdict(dict)
for s in splits:
    split_dic[s] = two_phase_attack(s)


--- Running split: 0 ---
Second phase perturbation rate: 0.1000
Phase 1: Added 0 edges out of requested 0.


Peturbing graph...:   0%|          | 0/527 [00:00<?, ?it/s]

OutOfMemoryError: CUDA out of memory. Tried to allocate 73.95 GiB. GPU 0 has a total capacity of 31.74 GiB of which 31.05 GiB is free. Including non-PyTorch memory, this process has 702.00 MiB memory in use. Of the allocated memory 300.69 MiB is allocated by PyTorch, and 19.31 MiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)